In [33]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [34]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if "workding_dir" not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/papers/rapget-translation


In [35]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/papers/rapget-translation/.env


True

In [36]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"
max_new_tokens = int(os.getenv("MAX_NEW_TOKENS", 2048))

print(
    model_name,
    adapter_name_or_path,
    load_in_4bit,
    data_path,
    results_path,
    use_english_datasets,
    max_new_tokens,
)

Qwen/Qwen2-7B-Instruct None False datasets/mac/mac.tsv results/mac-results.csv False 300


In [37]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, peft, torchaudio, torchvision, trl
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tok

In [38]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

MPS is available


In [39]:
df_openai = load_openai_training_data(
    data_path, openai_data_path="logs/openai-training-sample.jsonl"
)
df_openai

loading existing data from: logs/openai-training-sample.jsonl


messages
0  [{'role': 'system', 'content': 'Marv is a fact...
1  [{'role': 'system', 'content': 'Marv is a fact...
2  [{'role': 'system', 'content': 'Marv is a fact...

In [40]:
print_row_details(df_openai, range(len(df_openai)))

--------------------------------------------------
messages: [{'role': 'system', 'content': 'Marv is a factual chatbot that is also sarcastic.'}, {'role': 'user', 'content': "What's the capital of France?"}, {'role': 'assistant', 'content': "Paris, as if everyone doesn't know that already."}]
--------------------------------------------------
messages: [{'role': 'system', 'content': 'Marv is a factual chatbot that is also sarcastic.'}, {'role': 'user', 'content': "Who wrote 'Romeo and Juliet'?"}, {'role': 'assistant', 'content': 'Oh, just some guy named William Shakespeare. Ever heard of him?'}]
--------------------------------------------------
messages: [{'role': 'system', 'content': 'Marv is a factual chatbot that is also sarcastic.'}, {'role': 'user', 'content': 'How far is the Moon from Earth?'}, {'role': 'assistant', 'content': 'Around 384,400 kilometers. Give or take a few, like that really matters.'}]


In [41]:
df_openai = load_openai_training_data(data_path)
print_row_details(df_openai)

loading existing data from: datasets/mac/openai-training.jsonl
--------------------------------------------------
messages: [{'role': 'system', 'content': 'You are a helpful assistant that translates Chinese to English.'}, {'role': 'user', 'content': 'You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.\n\nChinese: 全仗着狐仙搭救。\nEnglish:'}, {'role': 'assistant', 'content': 'Because I was protected by a fox fairy.'}]


In [42]:
from openai import OpenAI

client = OpenAI()

client.files.create(
    file=open("datasets/mac/openai-training.jsonl", "rb"), purpose="fine-tune"
)

FileObject(id='file-IokPHn4YWcniXL4wGnK4xVmn', bytes=3413094, created_at=1723269681, filename='openai-training.jsonl', object='file', purpose='fine-tune', status='processed', status_details=None)

In [50]:
from openai import OpenAI

client = OpenAI()

client.fine_tuning.jobs.create(
    training_file="file-IokPHn4YWcniXL4wGnK4xVmn",
    model="gpt-4o-mini-2024-07-18",
    hyperparameters={"n_epochs": 6},
)

FineTuningJob(id='ftjob-TcCo4KtDd3Gp5cnOVky2Rxhh', created_at=1723270136, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=6, batch_size='auto', learning_rate_multiplier='auto'), model='gpt-4o-mini-2024-07-18', object='fine_tuning.job', organization_id='org-RXHVnD8cqPvqTPdXgZ5rQdl3', result_files=[], seed=1046194933, status='validating_files', trained_tokens=None, training_file='file-IokPHn4YWcniXL4wGnK4xVmn', validation_file=None, estimated_finish=None, integrations=[], user_provided_suffix=None)

In [52]:
from openai import OpenAI

client = OpenAI()

client.fine_tuning.jobs.retrieve("ftjob-TcCo4KtDd3Gp5cnOVky2Rxhh")

FineTuningJob(id='ftjob-TcCo4KtDd3Gp5cnOVky2Rxhh', created_at=1723270136, error=Error(code=None, message=None, param=None), fine_tuned_model='ft:gpt-4o-mini-2024-07-18:mastercard::9uaCEFTs', finished_at=1723272532, hyperparameters=Hyperparameters(n_epochs=6, batch_size=18, learning_rate_multiplier=1.8), model='gpt-4o-mini-2024-07-18', object='fine_tuning.job', organization_id='org-RXHVnD8cqPvqTPdXgZ5rQdl3', result_files=['file-aCppW0GWhhytwe4yKwymNUZl'], seed=1046194933, status='succeeded', trained_tokens=3640956, training_file='file-IokPHn4YWcniXL4wGnK4xVmn', validation_file=None, estimated_finish=None, integrations=[], user_provided_suffix=None)

In [56]:
datasets = load_translation_dataset(data_path, for_openai=True)
df_test = datasets["test"].to_pandas()
print_row_details(df_test, [100])

loading /Users/inflaton/code/engd/papers/rapget-translation/llm_toolkit/translation_utils.py


[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /Users/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     /Users/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


loading train/test data files


Map:   0%|          | 0/4528 [00:00<?, ? examples/s]

Map:   0%|          | 0/1133 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 然后他们到一间为游客开的通宵酒吧中去坐了两个多小时，沙瑞山一杯接着一杯地灌啤酒，变得更加健谈，而汪淼却早已心神不定，脑子里不断地浮现出那条绿色直线。
--------------------------------------------------
english: Then they went to an all-night bar for tourists and sat for two hours. As Sha finished one beer after another, his tongue loosened even more. But Wang became anxious, and his mind kept returning to that green line on the terminal in Sha's office.
--------------------------------------------------
text: [{'content': 'You are a helpful assistant that translates Chinese to English.', 'role': 'system'}
 {'content': 'You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text 

In [57]:
from openai import OpenAI

client = OpenAI()

completion = client.chat.completions.create(
    model="ft:gpt-4o-mini-2024-07-18:mastercard::9uaCEFTs",
    messages=df_test.iloc[100].prompt,
)
print(completion.choices[0].message)

ChatCompletionMessage(content="After that, they sat for more than two hours in an all-night bar open to hotel guests. Sha drank one cup of beer after another, becoming even more talkative. On the other hand, Wang's mind was no longer there. The green line floated constantly in his mind.", role='assistant', function_call=None, tool_calls=None, refusal=None)


In [60]:
from openai import OpenAI

client = OpenAI()

jobs = []
for epoch in range(1, 6):
    job = client.fine_tuning.jobs.create(
        training_file="file-IokPHn4YWcniXL4wGnK4xVmn",
        model="gpt-4o-mini-2024-07-18",
        seed=1046194933,
        hyperparameters={
            "n_epochs": epoch,
            "batch_size": 18,
            "learning_rate_multiplier": 1.8,
        },
        integrations=[
            {
                "type": "wandb",
                "wandb": {
                    "project": "OpenAI",
                    "name": f"gpt-4o-mini-2024-07-18-{epoch}",
                },
            },
        ],
    )
    jobs.append(job)

jobs

RateLimitError: Error code: 429 - {'error': {'message': "This fine-tune request has been rate-limited. Your organization has reached the maximum of 3 active requests (2 running, 1 pending) for the model 'gpt-4o-mini-2024-07-18'.", 'type': 'invalid_request_error', 'param': None, 'code': 'rate_limit_exceeded'}}

In [61]:
from openai import OpenAI

client = OpenAI()

jobs = []
for epoch in range(4, 6):
    job = client.fine_tuning.jobs.create(
        training_file="file-IokPHn4YWcniXL4wGnK4xVmn",
        model="gpt-4o-mini-2024-07-18",
        seed=1046194933,
        hyperparameters={
            "n_epochs": epoch,
            "batch_size": 18,
            "learning_rate_multiplier": 1.8,
        },
        integrations=[
            {
                "type": "wandb",
                "wandb": {
                    "project": "OpenAI",
                    "name": f"gpt-4o-mini-2024-07-18-{epoch}",
                },
            },
        ],
    )
    jobs.append(job)

jobs

[FineTuningJob(id='ftjob-LtXA4cTshuV3CVogO2jmRkMb', created_at=1723294897, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=4, batch_size=18, learning_rate_multiplier=1.8), model='gpt-4o-mini-2024-07-18', object='fine_tuning.job', organization_id='org-RXHVnD8cqPvqTPdXgZ5rQdl3', result_files=[], seed=1046194933, status='validating_files', trained_tokens=None, training_file='file-IokPHn4YWcniXL4wGnK4xVmn', validation_file=None, estimated_finish=None, integrations=[FineTuningJobWandbIntegrationObject(type='wandb', wandb=FineTuningJobWandbIntegration(project='OpenAI', entity=None, name=None, tags=None, run_id='ftjob-LtXA4cTshuV3CVogO2jmRkMb'))], user_provided_suffix=None),
 FineTuningJob(id='ftjob-ryBXC4G96hIWQ0M2csfwx42J', created_at=1723294900, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=5, batch_size=18, learning_rate_

In [67]:
fine_tuned_models = [
    "ft:gpt-4o-mini-2024-07-18:mastercard::9ufuULvy",
    "ft:gpt-4o-mini-2024-07-18:mastercard::9ug0Gt3w",
    "ft:gpt-4o-mini-2024-07-18:mastercard::9ug5PhpZ",
    "ft:gpt-4o-mini-2024-07-18:mastercard::9ugPThQI",
    "ft:gpt-4o-mini-2024-07-18:mastercard::9ugVLmcB",
    "ft:gpt-4o-mini-2024-07-18:mastercard::9uaCEFTs",
]

In [68]:
from llm_toolkit.eval_openai import evaluate_model_with_num_shots

In [69]:
for i, model in enumerate(fine_tuned_models):
    epoch = i + 1
    evaluate_model_with_num_shots(
        model,
        data_path,
        results_path="results/mac-results_few_shots_openai.csv",
        range_num_shots=[0],
        max_new_tokens=max_new_tokens,
        result_column_name=f"gpt-4o-mini/epochs-{epoch:02d}",
    )

Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9ufuULvy
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
*** Evaluating with num_shots: 0


100%|██████████| 1133/1133 [16:48<00:00,  1.12it/s]


gpt-4o-mini/epochs-01 metrics: {'meteor': 0.3785370331806402, 'sacrebleu': {'score': 12.052844230027103, 'counts': [12818, 4623, 2153, 1081], 'totals': [29097, 27964, 26850, 25740], 'precisions': [44.05265147609719, 16.53196967529681, 8.018621973929237, 4.1996891996892], 'bp': 0.9631327655852462, 'sys_len': 29097, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.12052844230027103, 'precisions': [0.44052651476097193, 0.1653196967529681, 0.08018621973929237, 0.041996891996891994], 'brevity_penalty': 0.9631327655852462, 'length_ratio': 0.9637959589267969, 'translation_length': 29097, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4244007719128182, 'rouge2': 0.17601540674784633, 'rougeL': 0.3693615986543504, 'rougeLsum': 0.3696442718692141}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9ug0Gt3w
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 45

100%|██████████| 1133/1133 [17:56<00:00,  1.05it/s]


gpt-4o-mini/epochs-02 metrics: {'meteor': 0.3785921332515917, 'sacrebleu': {'score': 12.033706874864837, 'counts': [12801, 4628, 2150, 1076], 'totals': [29076, 27943, 26830, 25722], 'precisions': [44.02600082542303, 16.562287513867517, 8.013417815877748, 4.183189487598165], 'bp': 0.9624112877781842, 'sys_len': 29076, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.12033706874864836, 'precisions': [0.4402600082542303, 0.16562287513867516, 0.08013417815877749, 0.04183189487598165], 'brevity_penalty': 0.9624112877781842, 'length_ratio': 0.9631003643590593, 'translation_length': 29076, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4235104923203792, 'rouge2': 0.1758318317686482, 'rougeL': 0.36922125683186846, 'rougeLsum': 0.3693808162149962}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9ug5PhpZ
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 

...

gpt-4o-mini/epochs-03 metrics: {'meteor': 0.37736228106121694, 'sacrebleu': {'score': 11.933111335430906, 'counts': [12779, 4601, 2124, 1061], 'totals': [29096, 27963, 26848, 25737], 'precisions': [43.920126477866376, 16.453885491542394, 7.911203814064362, 4.122469596301046], 'bp': 0.9630984208616785, 'sys_len': 29096, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11933111335430906, 'precisions': [0.4392012647786637, 0.16453885491542394, 0.07911203814064362, 0.041224695963010455], 'brevity_penalty': 0.9630984208616785, 'length_ratio': 0.9637628353759523, 'translation_length': 29096, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4235319934194407, 'rouge2': 0.17493309683581332, 'rougeL': 0.3685697120399035, 'rougeLsum': 0.3689298428303013}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9ugPThQI
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_row

100%|██████████| 1133/1133 [18:35<00:00,  1.02it/s]


gpt-4o-mini/epochs-04 metrics: {'meteor': 0.37818535038887346, 'sacrebleu': {'score': 11.933285526593995, 'counts': [12797, 4601, 2121, 1061], 'totals': [29110, 27977, 26861, 25749], 'precisions': [43.960838199931295, 16.445651785395146, 7.896206395889952, 4.120548370810517], 'bp': 0.9635791436286372, 'sys_len': 29110, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11933285526593994, 'precisions': [0.43960838199931296, 0.16445651785395146, 0.07896206395889951, 0.041205483708105166], 'brevity_penalty': 0.9635791436286371, 'length_ratio': 0.9642265650877774, 'translation_length': 29110, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.42372801674771476, 'rouge2': 0.17487358435014705, 'rougeL': 0.36931437347367646, 'rougeLsum': 0.36934766241132383}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9ugVLmcB
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num

  7%|▋         | 82/1133 [5:27:15<69:54:29, 239.46s/it]


KeyboardInterrupt: 

In [70]:
for i, model in enumerate(fine_tuned_models):
    epoch = i + 1
    if epoch < 5:
        continue
    
    evaluate_model_with_num_shots(
        model,
        data_path,
        results_path="results/mac-results_few_shots_openai.csv",
        range_num_shots=[0],
        max_new_tokens=max_new_tokens,
        result_column_name=f"gpt-4o-mini/epochs-{epoch:02d}",
    )

Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9ugVLmcB
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
*** Evaluating with num_shots: 0


100%|██████████| 1133/1133 [15:47<00:00,  1.20it/s]


gpt-4o-mini/epochs-05 metrics: {'meteor': 0.3790673551140706, 'sacrebleu': {'score': 11.955698498650582, 'counts': [12808, 4609, 2126, 1064], 'totals': [29209, 28076, 26959, 25846], 'precisions': [43.849498442260945, 16.416156147599374, 7.88604918580066, 4.116691170780778], 'bp': 0.9669721941455759, 'sys_len': 29209, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11955698498650584, 'precisions': [0.4384949844226095, 0.16416156147599373, 0.0788604918580066, 0.041166911707807785], 'brevity_penalty': 0.9669721941455759, 'length_ratio': 0.9675057966213978, 'translation_length': 29209, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.42476082012412075, 'rouge2': 0.17559955520032905, 'rougeL': 0.3700113513462385, 'rougeLsum': 0.37012014201963733}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-mini-2024-07-18:mastercard::9uaCEFTs
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows

100%|██████████| 1133/1133 [15:43<00:00,  1.20it/s]


gpt-4o-mini/epochs-06 metrics: {'meteor': 0.3792226866395673, 'sacrebleu': {'score': 11.982811850915233, 'counts': [12810, 4617, 2137, 1066], 'totals': [29116, 27983, 26868, 25757], 'precisions': [43.996428080780326, 16.499303148340065, 7.95369956825964, 4.138680746981403], 'bp': 0.9637850995333245, 'sys_len': 29116, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11982811850915229, 'precisions': [0.43996428080780325, 0.16499303148340064, 0.0795369956825964, 0.04138680746981403], 'brevity_penalty': 0.9637850995333245, 'length_ratio': 0.9644253063928453, 'translation_length': 29116, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4251187202203103, 'rouge2': 0.17553224521896635, 'rougeL': 0.37003282393672954, 'rougeLsum': 0.370114181474168}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
